In [2]:
using CSV
using DataFrames
using .IAI
using Random

# ---------------------------------------------------------
# Helper: get ENV with default
# ---------------------------------------------------------
getenv(key::AbstractString, default::AbstractString) = haskey(ENV, key) ? ENV[key] : default

# ---------------------------------------------------------
# 1. Resolve config from environment (mirroring Python script)
# ---------------------------------------------------------

train_data_file = getenv("TRAIN_DATA_FILE", "../data_gen/train_countdown_results_with_prompt_augmented_xgb.csv")
test_data_file  = getenv("TEST_DATA_FILE",  "../data_gen/test_countdown_results_with_prompt_gemini.csv")

# Column with the true label; default is "correct" to match your Python code
label_col_name = "correct"

# Random seed (optional, for reproducibility)
seed = parse(Int, getenv("RANDOM_STATE", "42"))

println("===================================================================")
println("OPTIMAL CLASSIFICATION TREE (IAI) - UNIFIED TRAIN/TEST")
println("===================================================================")
println("Train Data File: ", train_data_file)
println("Test Data File:  ", test_data_file)
println("Label column:    ", label_col_name)
println("Random seed:     ", seed)
println("===================================================================")

# ---------------------------------------------------------
# 2. Load train and test DataFrames
# ---------------------------------------------------------

println("Loading training data...")
train_df = CSV.read(train_data_file, DataFrame)
println("Training samples: ", nrow(train_df))

println("Training columns:")
println(names(train_df))

println("Loading test data...")
test_df = CSV.read(test_data_file, DataFrame)
println("Test samples:     ", nrow(test_df))

# Check label column
@assert label_col_name in names(train_df) "Label column $(label_col_name) not found in train data."
@assert label_col_name in names(test_df)  "Label column $(label_col_name) not found in test data."

# Ensure we only use columns that appear in BOTH train and test
common_cols = intersect(names(train_df), names(test_df))

train_df = train_df[:, common_cols]
test_df  = test_df[:, common_cols]

println("Number of columns common to train and test: ", length(common_cols))

# ---------------------------------------------------------
# 3. Build feature matrix X and label y
#    - Features: columns starting with "inst_" or "prompt_"
#    - Label:    column label_col_name
# ---------------------------------------------------------

feature_cols = [c for c in common_cols if startswith(String(c), "inst_") || startswith(String(c), "prompt_")]

if isempty(feature_cols)
    error("No feature columns found starting with 'inst_' or 'prompt_'. " *
          "Check that your CSV has those columns.")
end

println("Feature columns used (", length(feature_cols), "):")
println(feature_cols)

X_train = train_df[:, feature_cols]
y_train = train_df[:, label_col_name]

X_test  = test_df[:, feature_cols]
y_test  = test_df[:, label_col_name]

println("Train size: ", nrow(X_train))
println("Test size:  ", nrow(X_test))

# ---------------------------------------------------------
# 4. Fit Optimal Classification Tree on FULL training set
# ---------------------------------------------------------

Random.seed!(seed)

# Define a small hyperparameter grid (shallow interpretable trees)
grid = IAI.GridSearch(
    IAI.OptimalTreeClassifier(
        random_seed = seed,
        criterion   = :gini,   # you can switch to :misclassification if you prefer
    ),
    max_depth = 2:5,
    minbucket = 5:5:25,
)

println("\nFitting OptimalTreeClassifier grid search on full training set...")
IAI.fit!(grid, X_train, y_train)

OPTIMAL CLASSIFICATION TREE (IAI) - UNIFIED TRAIN/TEST
Train Data File: ../data_gen/train_countdown_results_with_prompt_augmented_xgb.csv
Test Data File:  ../data_gen/test_countdown_results_with_prompt_gemini.csv
Label column:    correct
Random seed:     42
Loading training data...
Training samples: 43445
Training columns:
["prompt_id", "instance_id", "prompt", "correct", "message", "inst_n_numbers", "inst_range", "inst_std", "inst_count_small", "inst_count_large", "inst_count_duplicates", "inst_count_even", "inst_count_odd", "inst_count_div_2", "inst_count_div_3", "inst_count_div_5", "inst_count_div_7", "inst_count_primes", "inst_distance_simple", "inst_distance_max", "inst_distance_avg", "inst_easy_pairs", "inst_log_target", "inst_expr_depth", "inst_count_add", "inst_count_sub", "inst_count_mul", "inst_count_div", "inst_noncomm_ops", "numbers", "target", "solution", "prompt_paraphrasing", "prompt_role-specification", "prompt_reasoning-trigger", "prompt_chain-of-thought", "prompt_self

All Grid Results:

 Row │ minbucket  max_depth  cp           train_score  valid_score  rank_valid_score
     │ Int64      Int64      Float64      Float64      Float64      Int64
─────┼───────────────────────────────────────────────────────────────────────────────
   1 │         5          2  0.00529449      0.623904     0.625141                16
   2 │         5          3  0.00122933      0.68424      0.687168                11
   3 │         5          4  9.68933e-5      0.717132     0.716345                 6
   4 │         5          5  2.35961e-5      0.743644     0.740807                 1
   5 │        10          2  0.00529449      0.623904     0.625141                17
   6 │        10          3  0.00122933      0.68424      0.687168                12
   7 │        10          4  8.68966e-5      0.717132     0.714271                10
   8 │        10          5  8.50408e-5      0.742643     0.740136                 3
   9 │        15          2  0.00529449      0.623904     0.625141                18
  10 │        15          3  0.00122933      0.68424      0.687168                13
  11 │        15          4  8.68966e-5      0.717132     0.714915                 8
  12 │        15          5  1.19208e-5      0.741796     0.740718                 2
  13 │        20          2  0.00529449      0.623904     0.625141                19
  14 │        20          3  0.00122933      0.68424      0.687168                14
  15 │        20          4  0.000149011     0.717132     0.714446                 9
  16 │        20          5  2.90414e-6      0.740882     0.738593                 4
  17 │        25          2  0.00529449      0.623904     0.625141                20
  18 │        25          3  0.00122933      0.68424      0.687168                15
  19 │        25          4  0.000165828     0.717132     0.71502                  7
  20 │        25          5  6.29326e-6      0.740173     0.737207                 5

Best Params:
  minbucket => 5
  cp => 2.359605304172452e-5
  max_depth => 5

Best Model - Fitted OptimalTreeClassifier:
  1) Split: inst_n_numbers < 3.5
    2) Split: prompt_chain-of-thought < 0.5
      3) Split: prompt_verbosity < 0.5
        4) Split: prompt_reasoning-trigger < 0.5
          5) Split: prompt_length < 214.5
            6) Predict: 1.0 (64.52%), [22,40], 62 points, error 0.4579
            7) Predict: 1.0 (97.46%), [246,9443], 9689 points, error 0.04949
          8) Split: inst_count_mul < 0.5
            9) Predict: 1.0 (94.95%), [195,3668], 3863 points, error 0.09586
            10) Predict: 1.0 (69.71%), [206,474], 680 points, error 0.4223
        11) Split: prompt_length < 788
          12) Split: inst_count_add < 0.5
            13) Predict: 0.0 (55.15%), [75,61], 136 points, error 0.4947
            14) Predict: 1.0 (85.02%), [96,545], 641 points, error 0.2547
          15) Split: inst_count_add < 0.5
            16) Predict: 0.0 (90.14%), [329,36], 365 points, error 0.1778
            17) Predict: 0.0 (54.90%), [767,630], 1397 points, error 0.4952
      18) Split: prompt_verbosity < 0.5
        19) Split: inst_count_sub < 0.5
          20) Split: prompt_length < 1041.5
            21) Predict: 0.0 (88.28%), [128,17], 145 points, error 0.207
            22) Predict: 1.0 (80.00%), [1,4], 5 points, error 0.32
          23) Split: inst_count_add < 0.5
            24) Predict: 0.0 (78.26%), [126,35], 161 points, error 0.3403
            25) Predict: 1.0 (72.33%), [176,460], 636 points, error 0.4003
        26) Split: prompt_id < 4569.5
          27) Split: inst_log_target < 1.966
            28) Predict: 0.0 (97.90%), [3028,65], 3093 points, error 0.04115
            29) Predict: 0.0 (84.01%), [247,47], 294 points, error 0.2686
          30) Split: inst_log_target < 1.929
            31) Predict: 0.0 (58.14%), [25,18], 43 points, error 0.4867
            32) Predict: 1.0 (100.00%), [0,8], 8 points, error 0
    33) Split: inst_count_div < 0.5
      34) Split: prompt_length < 545.5
 

In [3]:
best = IAI.get_learner(grid)

println("\n=================== Learned Optimal Classification Tree ===================")
display(best)
println("===========================================================================")

# ---------------------------------------------------------
# 5. Evaluate on train and test sets
# ---------------------------------------------------------

train_acc = IAI.score(best, X_train, y_train, criterion = :accuracy, positive_label = 1)
test_acc  = IAI.score(best, X_test,  y_test,  criterion = :accuracy, positive_label = 1)

println("\nTrain accuracy: ", train_acc)
println("Test accuracy:  ", test_acc)

# If binary labels, also compute AUC (optional)
unique_labels = unique(y_test)
if length(unique_labels) == 2
    try
        test_auc = IAI.score(best, X_test, y_test, criterion = :auc)
        println("Test AUC:       ", test_auc)
    catch e
        @warn "Could not compute AUC: $e"
    end
end

println("\nDone.")

Fitted OptimalTreeClassifier:
  1) Split: inst_n_numbers < 3.5
    2) Split: prompt_chain-of-thought < 0.5
      3) Split: prompt_verbosity < 0.5
        4) Split: prompt_reasoning-trigger < 0.5
          5) Split: prompt_length < 214.5
            6) Predict: 1.0 (64.52%), [22,40], 62 points, error 0.4579
            7) Predict: 1.0 (97.46%), [246,9443], 9689 points, error 0.04949
          8) Split: inst_count_mul < 0.5
            9) Predict: 1.0 (94.95%), [195,3668], 3863 points, error 0.09586
            10) Predict: 1.0 (69.71%), [206,474], 680 points, error 0.4223
        11) Split: prompt_length < 788
          12) Split: inst_count_add < 0.5
            13) Predict: 0.0 (55.15%), [75,61], 136 points, error 0.4947
            14) Predict: 1.0 (85.02%), [96,545], 641 points, error 0.2547
          15) Split: inst_count_add < 0.5
            16) Predict: 0.0 (90.14%), [329,36], 365 points, error 0.1778
            17) Predict: 0.0 (54.90%), [767,630], 1397 points, error 0.4952
      18) Split: prompt_verbosity < 0.5
        19) Split: inst_count_sub < 0.5
          20) Split: prompt_length < 1041.5
            21) Predict: 0.0 (88.28%), [128,17], 145 points, error 0.207
            22) Predict: 1.0 (80.00%), [1,4], 5 points, error 0.32
          23) Split: inst_count_add < 0.5
            24) Predict: 0.0 (78.26%), [126,35], 161 points, error 0.3403
            25) Predict: 1.0 (72.33%), [176,460], 636 points, error 0.4003
        26) Split: prompt_id < 4569.5
          27) Split: inst_log_target < 1.966
            28) Predict: 0.0 (97.90%), [3028,65], 3093 points, error 0.04115
            29) Predict: 0.0 (84.01%), [247,47], 294 points, error 0.2686
          30) Split: inst_log_target < 1.929
            31) Predict: 0.0 (58.14%), [25,18], 43 points, error 0.4867
            32) Predict: 1.0 (100.00%), [0,8], 8 points, error 0
    33) Split: inst_count_div < 0.5
      34) Split: prompt_length < 545.5
        35) Split: inst_count_mul < 0.5
          36) Split: prompt_reasoning-trigger < 0.5
            37) Predict: 1.0 (52.22%), [1181,1291], 2472 points, error 0.499
            38) Predict: 0.0 (93.27%), [1136,82], 1218 points, error 0.1256
          39) Split: inst_expr_depth < 2.5
            40) Predict: 0.0 (83.53%), [847,167], 1014 points, error 0.2751
            41) Predict: 0.0 (98.21%), [1591,29], 1620 points, error 0.03516
        42) Split: prompt_few-shot-count < 0.5
          43) Split: prompt_length < 624.5
            44) Predict: 0.0 (88.13%), [1321,178], 1499 points, error 0.2093
            45) Predict: 0.0 (98.52%), [5076,76], 5152 points, error 0.02907
          46) Split: inst_log_target < 1.906
            47) Predict: 0.0 (56.29%), [94,73], 167 points, error 0.4921
            48) Predict: 0.0 (84.62%), [55,10], 65 points, error 0.2604
      49) Split: inst_expr_depth < 2.5
        50) Split: inst_count_small < 2.5
          51) Split: inst_count_primes < 1.5
            52) Predict: 0.0 (97.40%), [1725,46], 1771 points, error 0.0506
            53) Predict: 0.0 (80.00%), [288,72], 360 points, error 0.32
          54) Split: prompt_length < 682.5
            55) Predict: 1.0 (96.67%), [1,29], 30 points, error 0.06444
            56) Predict: 0.0 (100.00%), [14,0], 14 points, error 0
        57) Split: inst_std < 16.03
          58) Split: inst_range < 38.5
            59) Predict: 0.0 (99.61%), [771,3], 774 points, error 0.007722
            60) Predict: 1.0 (53.85%), [12,14], 26 points, error 0.497
          61) Split: prompt_few-shot-count < 0.5
            62) Predict: 0.0 (99.05%), [5868,56], 5924 points, error 0.01873
            63) Predict: 0.0 (84.30%), [102,19], 121 points, error 0.2647


=================== Learned Optimal Classification Tree ===================

Train accuracy: 0.9112441017378294
Test accuracy:  0.8087318087318087
Test AUC:       0.8680696429839999

Done.
